In [1]:
import geopandas as gpd
import numpy as np
import folium
import pandas as pd
import matplotlib.pyplot as plt
from shapely.geometry import shape

In [2]:
# df = pd.read_csv('../validation_data/table_validation_bursts_priority_v0.1.csv')
df = pd.read_csv('../validation_data/table_validation_bursts_all_v0.1.csv')
df.columns = ['burst_id','Date','cslc_url','static_layer_url','geometry']
df['Date'] = pd.to_datetime(df['Date'],format='%Y%m%d')
df = df.drop_duplicates(subset=['burst_id'],ignore_index=True)
df

burst_id       Date  \
0     t004_006645_iw1 2015-03-10   
1     t004_006645_iw2 2015-03-10   
2     t004_006645_iw3 2015-03-10   
3     t004_006646_iw1 2015-03-10   
4     t004_006646_iw2 2015-03-10   
...               ...        ...   
1451  t160_342216_iw3 2014-10-28   
1452  t160_342217_iw1 2014-10-28   
1453  t160_342217_iw2 2014-10-28   
1454  t160_342217_iw3 2014-10-28   
1455  t160_342218_iw1 2014-10-28   

                                               cslc_url  \
0     s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
1     s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
2     s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
3     s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
4     s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
...                                                 ...   
1451  s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
1452  s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
1453  s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
1454  s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
1455  s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   

                                       static_layer_url  \
0     s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
1     s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
2     s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
3     s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
4     s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
...                                                 ...   
1451  s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
1452  s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
1453  s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
1454  s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   
1455  s3://opera-pst-rs-pop1/products/CSLC_S1/OPERA_...   

                                               geometry  
0     POLYGON ((-77.76543266245616 34.11769372469347...  
1     POLYGON ((-76.87849766663828 34.31499332258735...  
2     POLYGON ((-75.9426701785892 34.5121752079104, ...  
3     POLYGON ((-77.80459563512223 34.28499626973529...  
4     POLYGON ((-76.91565835604972 34.48165728994726...  
...                                                 ...  
1451  POLYGON ((-147.3432453594936 63.49086701606184...  
1452  POLYGON ((-144.0324536161071 63.12580718949295...  
1453  POLYGON ((-145.6807893022707 63.23310606393434...  
1454  POLYGON ((-147.4327540938831 63.32855820850803...  
1455  POLYGON ((-144.1213244640242 62.96170952346853...  

[1456 rows x 5 columns]

In [3]:
# Define ALE sites
ALE_sites = ['t042_088925_iw1',
't064_135523_iw1',
't064_135523_iw2',
't071_151224_iw2',
't094_200136_iw2',
't094_200136_iw3',
't107_227888_iw2',
't131_279917_iw1',
't137_292331_iw1',
't160_342208_iw3',
't160_342212_iw1']

# Read geometry column as wkt
df['geometry'] = gpd.GeoSeries.from_wkt(df['geometry'])
gdf = gpd.GeoDataFrame(df, crs="EPSG:4326", geometry=df.geometry)
gdf_ALE = gdf[gdf.burst_id.isin(ALE_sites)]
df = None

In [4]:
def getbasemaps():
    # Add custom base maps to folium
    basemaps = {
        'Google Satellite Hybrid': folium.TileLayer(
            tiles = 'https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}',
            attr = 'Google',
            name = 'Google Satellite',
            overlay = True,
            control = True,
            # opacity = 0.8,
            show = False
        ),
        'Esri Satellite': folium.TileLayer(
            tiles = 'https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
            attr = 'Esri',
            name = 'Esri Satellite',
            overlay = True,
            control = True,
            #opacity = 0.8,
            show = False
        )
    }
    return basemaps

In [5]:
# Interactive map
m = folium.Map(location=[40, -100], zoom_start=4.3, tiles="CartoDB positron")

# Add custom basemaps
basemaps = getbasemaps()
for basemap in basemaps:
    basemaps[basemap].add_to(m)

# layer Control
m.add_child(folium.LayerControl())

## RLE sites
for _, r in gdf.iterrows():
    sim_geo = gpd.GeoSeries(r["geometry"]).simplify(tolerance=0.001)
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j, style_function=lambda x: {"color": "red"}, control=False)
    folium.Popup(r["burst_id"]).add_to(geo_j)
    geo_j.add_to(m)

## ALE sites
for _, r in gdf_ALE.iterrows():
    sim_geo = gpd.GeoSeries(r["geometry"]).centroid
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j, style_function=lambda x: {"iconColor": "orange"}, control=False)
    folium.Popup(r["burst_id"]).add_to(geo_j)
    geo_j.add_to(m)

# Display
m

In [6]:
# Ridgecrest to LA
temp_ls = ['t064_135', 't071_151']


RIDGECREST_LA = [];
for ID in gdf['burst_id']:
    if ID[:8] in temp_ls:
        RIDGECREST_LA.append(ID)


In [7]:
df = pd.read_csv('../validation_data/validation_bursts_target_v0.1.csv')
df.columns = ['burst_id','cr_network']
gdf_priority = df.drop_duplicates(subset=['burst_id'],ignore_index=True)
gdf_priority

burst_id      cr_network
0   t004_006658_iw3        Virginia
1   t004_006660_iw3        Virginia
2   t034_071054_iw2            Katy
3   t034_071054_iw3         Houston
4   t034_071087_iw3        Oklahoma
5   t034_071088_iw2          Norman
6   t034_071089_iw2   Oklahoma_City
7   t042_088922_iw1  Central_Valley
8   t042_088925_iw1             SAF
9   t042_088926_iw1             SAF
10  t044_093110_iw1          Unimak
11  t064_135518_iw1              LA
12  t064_135523_iw1        Rosamond
13  t064_135523_iw2        Rosamond
14  t071_151224_iw2        Rosamond
15  t071_151228_iw1              LA
16  t071_151228_iw3              LA
17  t071_151230_iw2              LA
18  t087_185682_iw1      Big_Island
19  t087_185682_iw2      Big_Island
20  t087_185683_iw1      Big_Island
21  t087_185683_iw2      Big_Island
22  t094_200136_iw2          Alaska
23  t094_200136_iw3          Alaska
24  t098_209315_iw1     Puerto Rico
25  t098_209318_iw1     Puerto Rico
26  t106_225749_iw1        Virginia
27  t107_227886_iw3        Oklahoma
28  t107_227888_iw2        Oklahoma
29  t107_227889_iw1        Oklahoma
30  t124_264304_iw2      Big_Island
31  t124_264304_iw3      Big_Island
32  t124_264305_iw2      Big_Island
33  t124_264305_iw3      Big_Island
34  t124_264306_iw2      Big_Island
35  t124_264306_iw3      Big_Island
36  t124_264307_iw2      Big_Island
37  t124_264518_iw1          Unimak
38  t131_279917_iw1          Alaska
39  t135_287926_iw3     Puerto Rico
40  t135_287927_iw2     Puerto Rico
41  t137_292329_iw3  Central_Valley
42  t137_292330_iw1             SAF
43  t137_292331_iw1             SAF
44  t137_292379_iw1          Eugene
45  t143_305904_iw1         Houston
46  t143_305904_iw2            Katy
47  t143_305905_iw1         Houston
48  t144_308014_iw2  Central_Valley
49  t160_342208_iw3          Alaska
50  t160_342212_iw1          Alaska

In [8]:
#CENTRAL VALLEY sites
CENTRAL_VALLEY = ['t144_308014_iw2',
                    't144_308015_iw2',
                    't144_308016_iw2',
                    't042_088919_iw1',
                    't042_088920_iw1',
                    't042_088921_iw1',
                    't137_292335_iw1',
                    't137_292336_iw1',
                    't137_292337_iw1']

#ITHACA t106
ITHACA_t106 = []
temp_ls = list(range(225771, 225788))
for i in temp_ls:
    for iw in range(1,4):
        ITHACA_t106.append(f't106_{i}_iw{iw}')

#OREGON t137
OREGON_t137 = ['t137_292385_iw2']

#OREGON t115
OREGON_t115 = ['t115_245670_iw2']

#HAWAII t087
HAWAII_t087 = []
temp_ls = list(range(185673, 185691))
for i in temp_ls:
    for iw in range(1,4):
        HAWAII_t087.append(f't087_{i}_iw{iw}')

#HAWAII t124
HAWAII_t124 = []
temp_ls = list(range(264296, 264319))
for i in temp_ls:
    for iw in range(1,4):
        HAWAII_t124.append(f't124_{i}_iw{iw}')

In [9]:
temp_ls = HAWAII_t124 + HAWAII_t087 + OREGON_t115 + OREGON_t137 + ITHACA_t106 + CENTRAL_VALLEY + RIDGECREST_LA
temp_ls.sort()
to_keep_ = pd.DataFrame(temp_ls, columns=['burst_id'])

In [10]:
to_keep = pd.concat([gdf_priority['burst_id'], to_keep_['burst_id']]).sort_values(ignore_index=True).drop_duplicates()
to_keep

0      t004_006658_iw3
1      t004_006660_iw3
2      t034_071054_iw2
3      t034_071054_iw3
4      t034_071087_iw3
            ...       
425    t144_308014_iw2
427    t144_308015_iw2
428    t144_308016_iw2
429    t160_342208_iw3
430    t160_342212_iw1
Name: burst_id, Length: 412, dtype: object

In [11]:
to_keep_filtered = pd.DataFrame(to_keep, columns=['burst_id'])

geom = []
for ID in to_keep_filtered['burst_id']:
    try:
        geom.append(gdf.loc[gdf['burst_id']==ID, 'geometry'].iloc[0])
    except IndexError:
        geom.append(None)

to_keep_filtered['geometry'] = geom
to_keep_filtered = to_keep_filtered.drop_duplicates(subset=['burst_id'])
to_keep_filtered = to_keep_filtered.dropna()
to_keep_filtered['burst_id'].to_csv(f'../validation_data/to_keep_burst_ids_v0.1.csv', index=False)


In [12]:
# Interactive map
m = folium.Map(location=[40, -100], zoom_start=3, tiles="CartoDB positron")

# Add custom basemaps
basemaps = getbasemaps()
for basemap in basemaps:
    basemaps[basemap].add_to(m)

# layer Control
m.add_child(folium.LayerControl())

## RLE sites
for _, r in to_keep_filtered.iterrows():
    sim_geo = gpd.GeoSeries(r["geometry"]).simplify(tolerance=0.001)
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j, style_function=lambda x: {"color": "red"}, control=False)
    folium.Popup(r["burst_id"]).add_to(geo_j)
    geo_j.add_to(m)


## ALE sites
for _, r in gdf_ALE.iterrows():
    sim_geo = gpd.GeoSeries(r["geometry"]).centroid
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j, style_function=lambda x: {"iconColor": "orange"}, control=False)
    folium.Popup(r["burst_id"]).add_to(geo_j)
    geo_j.add_to(m)

# Display
m